 # "СберАвтоподписка": разработка модели, предсказывающей целевое событие  

---

**Цель проекта**: разработать модель предсказания совершения одного из целевых действий ("Заказать звонок", "Оставить заявку") для сессий по введенным атрибутам типа utm_*, device_*, geo_* и упаковать модель в сервис.



**Целевая метрика**: ориентировочное значение roc-auc > 0.65 — факт совершения
пользователем целевого действия.

**Формат вывода ответа** - 0/1

**Скорость ответа сервиса** - не более 3 секунд

**Сервис** - это должен быть (минимум) - py-скрипт с инструкцией по запуску, (максимум) - localhost web app.

---

В данной работе я буду использовать библиотеку Feuture-engine.

Вот небольшая характеристика Feature-engine:

* Feature-engine содержит наиболее исчерпывающую коллекцию преобразований для разработки функций.

* Feature-engine может преобразовывать определенную группу переменных в фрейм данных.

* Feature-engine возвращает кадры данных, поэтому подходит для исследования данных и развертывания модели.

* Feature-engine совместим с конвейером Scikit-learn, грид- и случайным поиском и перекрестной проверкой.

* Feature-engine автоматически распознает числовые, категориальные переменные и переменные даты и времени.

* Feature-engine предупреждает вас, если преобразование невозможно, например, если применяется логарифмирование к отрицательным переменным или деление на 0.




### Импорт библиотек

#### Перед импортом библиотек предварительно устанавливается:
* `pip install xgboost` согласно [документации](https://xgboost.readthedocs.io/en/stable/install.html#python)
* `pip install lightgbm` согласно [документации](https://github.com/microsoft/LightGBM/tree/master/python-package)
* `pip install bayesian-optimization` согласно [документации](https://github.com/fmfn/BayesianOptimization)
* `pip install feature-engine`
* `pip install bayesian-optimization`
* `pip install colorama`

In [6]:
!pip install feature-engine

In [7]:
!pip install bayesian-optimization


In [8]:
!pip install lightgbm


In [9]:
import sys
from datetime import datetime
import warnings
from pathlib import Path
from typing import Union
from functools import partial


import dill
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

# препроцессинг и метрики
from sklearn.preprocessing import FunctionTransformer, StandardScaler
from sklearn.model_selection import (
    train_test_split, GridSearchCV, StratifiedKFold)
from sklearn.metrics import (
    roc_auc_score, accuracy_score, confusion_matrix, precision_score, 
    recall_score, f1_score, make_scorer, roc_curve)
from sklearn.pipeline import Pipeline
from feature_engine.encoding import RareLabelEncoder, OneHotEncoder
from feature_engine.wrappers import SklearnTransformerWrapper
from feature_engine.outliers import Winsorizer
from feature_engine.selection import (
    DropDuplicateFeatures, DropConstantFeatures, 
    DropCorrelatedFeatures, DropFeatures)
from feature_engine.transformation import YeoJohnsonTransformer
from bayes_opt import BayesianOptimization

# модели
from sklearn.base import BaseEstimator
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.svm import LinearSVC
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import (
    RandomForestClassifier, HistGradientBoostingClassifier)
from catboost import CatBoostClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier

# дополнительные данные
from additional_data import (
    get_distance_from_moscow, target_events, missing_values, organic_mediums, 
    social_media_sources, moscow_region_cities, big_cities, russian_holidays)

### Создание констант

In [11]:
# необходимо указать путь к папкам с данными и моделями

data_folder = Path('..', 'data')
models_folder = Path('.', 'models')

sessions_filename = 'ga_sessions.csv'
hits_filename = 'ga_hits.csv'

In [12]:
TEST_SIZE = 200_000
RANDOM_SEED = 0

### Настройка ноутбука

In [14]:
pd.set_option('display.max_columns', 100)
warnings.filterwarnings('ignore')

### Загрузка данных

Для файла `ga_hits.csv` нужно загрузить только колонки 'session_id' и 'event_action', так как остальные не используются.

In [16]:
from pathlib import Path
import pandas as pd

data_folder      = Path('data')
sessions_path    = data_folder / 'ga_sessions.csv'
hits_path        = data_folder / 'ga_hits.csv'

print("Looking at:", sessions_path.resolve())
print("Exists?   ", sessions_path.exists())

sessions = pd.read_csv(sessions_path)
hits     = pd.read_csv(hits_path, usecols=['session_id', 'event_action'])

Looking at: C:\Users\USER\Desktop\hakaton\data\ga_sessions.csv
Exists?    True


In [17]:
sessions = pd.read_csv(data_folder / sessions_filename)
hits = pd.read_csv(data_folder / hits_filename, 
                   usecols=['session_id', 'event_action'])

In [18]:
sessions.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1860042 entries, 0 to 1860041
Data columns (total 18 columns):
 #   Column                    Dtype 
---  ------                    ----- 
 0   session_id                object
 1   client_id                 object
 2   visit_date                object
 3   visit_time                object
 4   visit_number              int64 
 5   utm_source                object
 6   utm_medium                object
 7   utm_campaign              object
 8   utm_adcontent             object
 9   utm_keyword               object
 10  device_category           object
 11  device_os                 object
 12  device_brand              object
 13  device_model              object
 14  device_screen_resolution  object
 15  device_browser            object
 16  geo_country               object
 17  geo_city                  object
dtypes: int64(1), object(17)
memory usage: 1.7 GB


In [19]:
hits.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15726470 entries, 0 to 15726469
Data columns (total 2 columns):
 #   Column        Dtype 
---  ------        ----- 
 0   session_id    object
 1   event_action  object
dtypes: object(2)
memory usage: 2.2 GB


## Подготовка данных

### Целевая переменная  

Целевая переменная считается положительной, если для сессии из `sessions` есть хотя бы одно целевое событие в `hits`. 

In [22]:
hits['target'] = hits['event_action'].isin(target_events) # заполняет столбец hits['target'] 'True', если hits['event_action'] содержит целевую
is_target_event = hits.groupby('session_id')['target'].any().astype(int) # target группирует по id (session_id) и по столбцу 'target', то есть все одинаковые session_id собираются

In [23]:
hits['target']

0           False
1           False
2           False
3           False
4           False
            ...  
15726465    False
15726466    False
15726467    False
15726468    False
15726469    False
Name: target, Length: 15726470, dtype: bool

In [24]:
is_target_event

session_id
1000009318903347362.1632663668.1632663668    0
1000010177899156286.1635013443.1635013443    0
1000013386240115915.1635402956.1635402956    0
1000017303238376207.1623489300.1623489300    0
1000020580299877109.1624943350.1624943350    0
                                            ..
999960188766601545.1626816843.1626816843     0
99996598443387715.1626811203.1626811203      0
999966717128502952.1638428330.1638428330     0
999988617151873171.1623556243.1623556243     0
999989480451054428.1634311006.1634311006     0
Name: target, Length: 1734610, dtype: int32

In [25]:
target = pd.Series(is_target_event, index=sessions['session_id']).fillna(0.0) # Заполним пропуски 0,0
target.value_counts(dropna=False, normalize=True) # посчитаем значения, так и есть - целевых значений  2,7%

target
0.0    0.97295
1.0    0.02705
Name: proportion, dtype: float64

In [26]:
target

session_id
9055434745589932991.1637753792.1637753792    0.0
905544597018549464.1636867290.1636867290     0.0
9055446045651783499.1640648526.1640648526    0.0
9055447046360770272.1622255328.1622255328    0.0
9055447046360770272.1622255345.1622255345    0.0
                                            ... 
9055415581448263752.1640159305.1640159305    0.0
9055421130527858185.1622007305.1622007305    0.0
9055422955903931195.1636979515.1636979515    0.0
905543020766873816.1638189404.1638189404     0.0
9055430416266113553.1640968742.1640968742    0.0
Name: target, Length: 1860042, dtype: float64

In [27]:
del hits # удалим датафрейм за ненадобностью чтобы не занимал много памяти

### Заполнение пропусков  

Пропуски в колонке `device_screen_resolution` заполняем самым частым значением.  
Все остальные пропуски в колонках заполняем значением '(nan)'.

In [29]:
def fill_missings(data: pd.DataFrame) -> pd.DataFrame:
    """Заполняет пропущенные значения:
    * самым частым значением для `device_screen_resolution`;
    * значением '(nan)' во всех остальных случаях.
    """

    data = data.copy()

    if 'device_screen_resolution' in data.columns:
        # '414x896' - самое частое значение в 'device_screen_resolution'
        # согласно предварительному анализу данных
        data['device_screen_resolution'] = \
            data['device_screen_resolution'].replace(missing_values, '414x896')
    
    return data.fillna('(nan)')

### Генерация признаков

Создаётся множество дополнительных переменных: день недели и день месяца, является ли день выходным, час и минута посещения, ночью ли посещение, ширина, высота, площадь и соотношение экрана.

В том числе с дополнительными данными: является ли день празничным, является ли трафик органическим, из социальных ли сетей он, находится ли пользователь в большом городе или в московской области, расстояние до Москвы как численно, так и в виде категорий.

In [31]:
def distance_category(distance: float) -> str:
    """Возвращает категорию расстояния до Москвы."""

    if distance == -1: return 'no distance'
    elif distance == 0: return 'moscow'
    elif distance < 100: return '< 100 km'
    elif distance < 500: return '100-500 km'
    elif distance < 1000: return '500-1000 km'
    elif distance < 3000: return '1000-3000 km'
    else: return '>= 3000 km'

In [32]:
def create_features(data: pd.DataFrame) -> pd.DataFrame:
    """Создаёт новые признаки из существующих."""

    data = data.copy()
    
    # visit_date признаки 
    if 'visit_date' in data.columns:
        data['visit_date'] = data['visit_date'].astype('datetime64[ns]')
        data['visit_date_added_holiday'] = \
            data['visit_date'].isin(russian_holidays)
        # числовые признаки сделаем строго положительными 
        # для лучшей обработки на шаге с YeoJohnsonTransformer
        data['visit_date_weekday'] = data['visit_date'].dt.weekday + 1
        data['visit_date_weekend'] = data['visit_date'].dt.weekday > 4
        data['visit_date_day'] = data['visit_date'].dt.day + 1

    # visit_time признаки
    if 'visit_time' in data.columns:
        data['visit_time'] = data['visit_time'].astype('datetime64[ns]')
        data['visit_time_hour'] = data['visit_time'].dt.hour + 1
        data['visit_time_minute'] = data['visit_time'].dt.minute + 1
        data['visit_time_night'] = data['visit_time'].dt.hour < 9

    # utm_* признаки
    if 'utm_medium' in data.columns:
        data['utm_medium_added_is_organic'] = \
            data['utm_medium'].isin(organic_mediums)
    if 'utm_source' in data.columns: 
        data['utm_source_added_is_social'] = \
            data['utm_source'].isin(social_media_sources)
    
    # device_screen признаки
    if 'device_screen_resolution' in data.columns:
        name = 'device_screen_resolution'
        data[[name + '_width', name + '_height']] = \
            data[name].str.split('x', expand=True).astype(float)
        data[name + '_area'] = data[name + '_width'] * data[name + '_height']
        data[name + '_ratio'] = data[name + '_width'] / data[name + '_height']
        data[name + '_ratio_greater_1'] = data[name + '_ratio'] > 1

    # geo_city признаки 
    if 'geo_city' in data.columns:
        data['geo_city_added_is_moscow_region'] = \
            data['geo_city'].isin(moscow_region_cities)
        data['geo_city_added_is_big'] = data['geo_city'].isin(big_cities)
        data['geo_city_is_big_or_in_moscow_region'] = \
            data['geo_city_added_is_moscow_region'] \
            | data['geo_city_added_is_big']
        data['geo_city_added_distance_from_moscow'] = \
            data['geo_city'].apply(get_distance_from_moscow)
        data['geo_city_added_distance_from_moscow_category'] = \
            data['geo_city_added_distance_from_moscow'].apply(distance_category)

    return data

### Дополнительно

In [34]:
def set_index(data: pd.DataFrame, column: str = 'session_id') -> pd.DataFrame:
    """Устанавливает в качестве индекса датафрейма колонку `column`."""
    
    data = data.copy()

    if column in data.columns:
        data = data.set_index(column)
    
    return data

In [35]:
def converse_types(data: pd.DataFrame) -> pd.DataFrame:
    """Приводит типы переменных к float. В первую очередь 
    необходимо для преобразования bool значений.
    """

    return data.astype(float)

### Собираем пайплайн  

Пайплайн по подготовке данных состоит из 4 частей:  
1. Создание дополнительных признаков
2. Преобразование численных переменных
3. Преобразование категориальных переменных
4. Удаление лишних признаков

In [37]:
preprocessor = Pipeline(steps=[

    # Создание дополнительных признаков и
    # Приведение датафрейма к удобному виду 
    ('indexer', FunctionTransformer(set_index)), 
    ('imputer', FunctionTransformer(fill_missings)), 
    ('engineer', FunctionTransformer(create_features)), 
    ('dropper', DropFeatures(['client_id', 'visit_date', 'visit_time', 
                              'device_screen_resolution'])), 

    # Преобразования численных переменных
    ('normalization', YeoJohnsonTransformer()), 
    ('outlier_remover', Winsorizer()), 
    ('scaler', SklearnTransformerWrapper(StandardScaler())), 

    # Преобразования категориальных признаков
    ('rare_encoder', RareLabelEncoder(tol=0.05, replace_with='rare')), 
    ('onehot_encoder', OneHotEncoder(drop_last_binary=True)), 
    ('bool_converter', FunctionTransformer(converse_types)), 

    # Удаление дубликатов и коррелируемых признаков
    ('constant_dropper', DropConstantFeatures(tol=0.99)), 
    ('duplicated_dropper', DropDuplicateFeatures()), 
    ('correlated_dropper', DropCorrelatedFeatures(threshold=0.8)), 

])

## Моделирование

### Разделение данных  

Разделим данные на тренировочную, валидационную и тестовую выборки.  


In [40]:
X, X_test, y, y_test = train_test_split(
    sessions, target, test_size=TEST_SIZE, 
    stratify=target, random_state=RANDOM_SEED)

X_train, X_valid, y_train, y_valid = train_test_split(
    X, y, test_size=TEST_SIZE, 
    stratify=y, random_state=RANDOM_SEED)

print(f'train shapes: {X_train.shape} {y_train.shape}')
print(f'valid shapes: {X_valid.shape} {y_valid.shape}')
print(f'test  shapes: {X_test.shape} {y_test.shape}')

train shapes: (1460042, 18) (1460042,)
valid shapes: (200000, 18) (200000,)
test  shapes: (200000, 18) (200000,)


### Препроцессинг данных  

Преобразуем тренировочные и валидационные данные с помощью построенного конвейера.

In [42]:
X_train

session_id             client_id  \
1056663   547332070992313735.1638727047.1638727047      127435678.163873   
1409550  7049980726847853060.1629809978.1629809978     1641451550.162934   
739873   4064566220882386809.1639930788.1639930788      946355569.163992   
62902    1033849280328168809.1631647080.1631647080      240711793.163165   
1297234  6544287746962620171.1638268683.1638268683     1523710728.163827   
...                                            ...                   ...   
1793000  8755082352522037809.1633552946.1633552946     2038451459.163355   
207261   1682284231298311525.1640424805.1640424805  391687320.1640424805   
93412    1170303784354950884.1640345317.1640345317      272482583.164035   
1568591  7753976912353269271.1634047522.1634047522     1805363435.163405   
1119538  5753600408244704247.1626854393.1626854393     1339614486.162685   

         visit_date visit_time  visit_number            utm_source utm_medium  \
1056663  2021-12-05   20:57:27             1  ZpYIoDJMcFzVoPFsHGJL     banner   
1409550  2021-08-24   15:00:00             5  MvfHsxITijuriZxsqZqt        cpm   
739873   2021-12-19   19:19:48             2  ZpYIoDJMcFzVoPFsHGJL     banner   
62902    2021-09-14   22:00:00             1  ZpYIoDJMcFzVoPFsHGJL     banner   
1297234  2021-11-30   13:38:03             1  ZpYIoDJMcFzVoPFsHGJL     banner   
...             ...        ...           ...                   ...        ...   
1793000  2021-10-06   23:00:00             1  fDLlAcSmythWSCVMvqvL     (none)   
207261   2021-12-25   12:33:25             1  fDLlAcSmythWSCVMvqvL     (none)   
93412    2021-12-24   14:28:37             1  fDLlAcSmythWSCVMvqvL     (none)   
1568591  2021-10-12   17:00:00             1  ZpYIoDJMcFzVoPFsHGJL     banner   
1119538  2021-07-21   10:00:00             1  MvfHsxITijuriZxsqZqt        cpm   

                 utm_campaign         utm_adcontent           utm_keyword  \
1056663  TmThBvoCcwkCZZUWACYq  JNHcPlZPxEMWDnRiyoBf  puhZPIYqKXeFPaUviSjo   
1409550  FTjNLDyTrXaWYgZymFkV  PkybGvWbaqORmxjNunqZ                   NaN   
739873   LEoPHuyFvzoNfnzGgfcd  vCIpmpaGBnIQhyYNkXqp  puhZPIYqKXeFPaUviSjo   
62902    gecBYcKZCPMcVYdSSzKP  JNHcPlZPxEMWDnRiyoBf                   NaN   
1297234  LEoPHuyFvzoNfnzGgfcd  vCIpmpaGBnIQhyYNkXqp  puhZPIYqKXeFPaUviSjo   
...                       ...                   ...                   ...   
1793000  LTuZkdKfxRGVceoWkVyg  JNHcPlZPxEMWDnRiyoBf                   NaN   
207261   LTuZkdKfxRGVceoWkVyg  JNHcPlZPxEMWDnRiyoBf  puhZPIYqKXeFPaUviSjo   
93412    LTuZkdKfxRGVceoWkVyg  JNHcPlZPxEMWDnRiyoBf  puhZPIYqKXeFPaUviSjo   
1568591  gecBYcKZCPMcVYdSSzKP  JNHcPlZPxEMWDnRiyoBf                   NaN   
1119538  FTjNLDyTrXaWYgZymFkV  dUuXlWzvmhDSyclWRhNP                   NaN   

        device_category device_os device_brand device_model  \
1056663          mobile       iOS        Apple          NaN   
1409550          mobile       NaN       Xiaomi          NaN   
739873           mobile   Android      Samsung          NaN   
62902            mobile       NaN        Apple          NaN   
1297234          mobile   Android       Xiaomi          NaN   
...                 ...       ...          ...          ...   
1793000          mobile       NaN      Samsung          NaN   
207261           mobile       iOS        Apple          NaN   
93412           desktop   Windows          NaN          NaN   
1568591          mobile       NaN       Xiaomi          NaN   
1119538          mobile       NaN       Xiaomi          NaN   

        device_screen_resolution device_browser geo_country          geo_city  
1056663                  428x926         Safari      Russia       Novotroitsk  
1409550                  393x851         Chrome      Russia        Balashikha  
739873                   339x753         Chrome      Russia        Almetyevsk  
62902                    414x896         Safari      Russia  Saint Petersburg  
1297234                  393x851         Chrome      Russia            M

In [43]:
X_train_preprocessed = preprocessor.fit_transform(X_train)
X_valid_preprocessed = preprocessor.transform(X_valid)

print(f'X_train.shape = {X_train_preprocessed.shape}')

X_train.shape = (1460042, 55)


### Выбор метрик  

Будем использовать в качестве основной метрики - `roc_auc`. Но также взглянем и на другие метрики: `accuracy`, `precision`, `recall`, `f1`.  


In [45]:
def find_best_threshold(
    y_true: pd.Series, 
    y_proba: pd.Series, 
    metriс_name: str = 'roc_auc', 
    iterations: int = 250, 
    learning_rate: float = 0.05
) -> float:
    """Находит лучший порог перевода вероятностей `y_proba` 
    в принадлежность к классу 1.
    """
    
    # Получение функции метрики, которую оптимизируем
    metrics = {'roc_auc': roc_auc_score, 'f1': f1_score, 
               'precision': precision_score, 'recall': recall_score}
    metric_function = metrics.get(metriс_name, accuracy_score)

    # Получение метрики
    def get_metric(threshold: float) -> float:
        prediction = (y_proba > threshold).astype(int)
        return metric_function(y_true, prediction)

    direction = -1
    shift = 0.25

    best_threshold = 0.5
    best_metric = get_metric(best_threshold)

    # На каждой итерации
    for i in range(iterations):

        # Меняем порог
        threshold = best_threshold + direction * shift
        shift *= (1 - learning_rate)
        metric = get_metric(threshold)

        # И проверяем, улучшилась ли метрика
        if metric > best_metric: 
            best_threshold = threshold
            best_metric = metric
        else: 
            direction *= -1
            
    return best_threshold

In [46]:
def print_metrics(
    model: BaseEstimator, 
    X: pd.DataFrame, 
    y: pd.Series, 
    threshold: Union[float, None] = None, 
    show_roc_curve: bool = False
) -> None:
    """Получает метрики бинарной классификации из модели `model` на данных 
    `X` и `y`. Если возможно, то через метод `predict_proba` с заданным 
    порогом перевода вероятностей в классы `threshold`, иначе через `predict`. 
    Если `threshold` равен None, автоматически найдёт лучший порог.  
    ---
    Метрики: roc_auc, accuracy, precision, recall, f1, confusion_matrix, 
    roc_curve.
    """

    # Получим предсказания, если возможно в виде вероятностей
    try: 
        probas = model.predict_proba(X)[:, 1]
    except AttributeError:
        prediction = model.predict(X)
        threshold = None
        probas = None
    else:
        threshold = threshold or find_best_threshold(y, probas, 'roc_auc')
        prediction = (probas > threshold).astype(int)

    # Распечатаем порог перевода вероятностей в классы
    if threshold is None:
        print("Порог перевода вероятностей в классы: не используется")
    else:
        print(f"Порог перевода вероятностей в классы: {threshold}")
        print(f"{roc_auc_score(y, probas)} - roc_auc на вероятностях")

    # Распечатаем однострочные метрики
    print()
    print(f"{roc_auc_score(y, prediction):0.8f} - roc_auc")
    print(f"{accuracy_score(y, prediction):0.8f} - accuracy")
    print(f"{precision_score(y, prediction):0.8f} - precision")
    print(f"{recall_score(y, prediction):0.8f} - recall")
    print(f"{f1_score(y, prediction):0.8f} - f1")

    # Распечатаем матрицу ошибок
    conf_mat = confusion_matrix(y, prediction)
    classes = model.classes_
    n_classes = len(classes)
    print()
    print("|".join(f"{i:^10}" for i in ["prediction"] + list(classes)))
    print(f"{'true label':^10}" + ("|" + " " * 10) * n_classes)
    print("-" * ((n_classes * 10) + n_classes + 10))
    for i in range(n_classes):
        print("|".join(f"{j:>10}" for j in [classes[i]] + list(conf_mat[i])))

    # Отобразим ROC-кривую
    if show_roc_curve:
        print()
        plt.figure(figsize=(7, 4))
        if probas is not None:
            plt.plot(*roc_curve(y_test, probas)[:2], 
                     c='r', label='on probability')
        plt.plot(*roc_curve(y_test, prediction)[:2], c='b', label='on class')
        plt.plot([0, 1], [0, 1], c='y', label='random', linestyle='dashed')
        plt.title('Receiver operating characteristic')
        plt.xlabel('False Positive Rate')
        plt.ylabel('True Positive Rate')
        plt.legend()
        plt.show()

### Базовая модель  

Так как целевая переменная распределена не равномерно, то в качестве бейзлайна можно выбрать стратегию, которая для каждой сессии предсказывает значение 0.  


In [48]:
# Обучим базовую модель 
baseline = DummyClassifier(strategy='constant', constant=0)
baseline.fit(X_train_preprocessed, y_train)

# И получим её метрики
print_metrics(baseline, X_valid_preprocessed, y_valid, 0.5)

Порог перевода вероятностей в классы: 0.5
0.5 - roc_auc на вероятностях

0.50000000 - roc_auc
0.97295000 - accuracy
0.00000000 - precision
0.00000000 - recall
0.00000000 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    194590|         0
       1.0|      5410|         0


### Выбор модели  

Обучим несколько моделей, оценим на валидационной выборке и выберем лучшую, которую уже будем оптимизировать.

#### Логистическая регрессия

In [51]:
logreg = LogisticRegression(random_state=RANDOM_SEED)

In [52]:
%%time
logreg.fit(X_train_preprocessed, y_train);

CPU times: total: 3.77 s
Wall time: 2.59 s


In [53]:
print_metrics(logreg, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.5
0.666948684655609 - roc_auc на вероятностях

0.50000000 - roc_auc
0.97295000 - accuracy
0.00000000 - precision
0.00000000 - recall
0.00000000 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    194590|         0
       1.0|      5410|         0


#### Метод опорных векторов

In [55]:
svc = LinearSVC(class_weight='balanced')


In [56]:
%%time
svc.fit(X_train_preprocessed, y_train);

CPU times: total: 5min 14s
Wall time: 7min 6s


In [57]:
print_metrics(svc, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: не используется

0.62031567 - roc_auc
0.59197500 - accuracy
0.04226790 - precision
0.65027726 - recall
0.07937636 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    114877|     79713
       1.0|      1892|      3518


#### Нейронная сеть

In [59]:
mlp = MLPClassifier((32,), random_state=RANDOM_SEED)

In [60]:
%%time
mlp.fit(X_train_preprocessed, y_train);

CPU times: total: 9.48 s
Wall time: 58 s


In [61]:
print_metrics(mlp, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.02765309611660135
0.6965179795539586 - roc_auc на вероятностях

0.64160291 - roc_auc
0.60874500 - accuracy
0.04564678 - precision
0.67634011 - recall
0.08552163 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    118090|     76500
       1.0|      1751|      3659


In [87]:
!pip install alive-progress


     ---------------------------------------- 0.0/70.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/70.6 kB ? eta -:--:--
     ----------------- ---------------------- 30.7/70.6 kB ? eta -:--:--
     -------------------------------------- 70.6/70.6 kB 773.7 kB/s eta 0:00:00
     ---------------------------------------- 0.0/207.3 kB ? eta -:--:--
     --------------- ----------------------- 81.9/207.3 kB 4.5 MB/s eta 0:00:01
     ------------------------------ ------- 163.8/207.3 kB 2.0 MB/s eta 0:00:01
     ------------------------------ ------- 163.8/207.3 kB 2.0 MB/s eta 0:00:01
     ------------------------------- ------ 174.1/207.3 kB 1.2 MB/s eta 0:00:01
     --------------------------------- -- 194.6/207.3 kB 908.0 kB/s eta 0:00:01
     --------------------------------- -- 194.6/207.3 kB 908.0 kB/s eta 0:00:01
     --------------------------------- -- 194.6/207.3 kB 908.0 kB/s eta 0:00:01
     ------------------------------------ 207.3/207.3 kB 600.8 kB/s et

In [89]:
from alive_progress import alive_bar
import time

for x in 1000, 1500, 700, 0:
   with alive_bar(x) as bar:
       for i in range(1000):
           time.sleep(.005)
           bar()

|████████████████████████████████████████| 1000/1000 [100%] in 5.3s (188.41/s) 
|██████████████████████████▋⚠︎            | (!) 1000/1500 [67%] in 5.3s (189.12/s) 
|████████████████████████████████████████✗︎ (!) 1000/700 [143%] in 5.4s (186.71/s) 
|████████████████████████████████████████| 1000 in 5.4s (186.05/s) 


#### Байесовский классификатор

In [91]:
gaussnb = GaussianNB()

In [93]:
%%time
gaussnb.fit(X_train_preprocessed, y_train);

CPU times: total: 188 ms
Wall time: 904 ms


In [95]:
print_metrics(gaussnb, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.07742572635680028
0.6450723123332731 - roc_auc на вероятностях

0.60849806 - roc_auc
0.57912000 - accuracy
0.04037999 - precision
0.63955638 - recall
0.07596382 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    112364|     82226
       1.0|      1950|      3460


#### Дерево решений

In [97]:
tree = DecisionTreeClassifier(random_state=RANDOM_SEED)

In [99]:
%%time
tree.fit(X_train_preprocessed, y_train);

CPU times: total: 4.86 s
Wall time: 13.9 s


In [101]:
print_metrics(tree, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.03813526168830234
0.522175966644499 - roc_auc на вероятностях

0.52279755 - roc_auc
0.93024000 - accuracy
0.05221220 - precision
0.09205176 - recall
0.06663099 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    185550|      9040
       1.0|      4912|       498


#### Случайный лес

In [103]:
forest = RandomForestClassifier(random_state=RANDOM_SEED)

In [105]:
%%time
forest.fit(X_train_preprocessed, y_train);

CPU times: total: 1min 11s
Wall time: 2min 58s


In [107]:
print_metrics(forest, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.020252250711307138
0.6231388770493229 - roc_auc на вероятностях

0.59364739 - roc_auc
0.71947000 - accuracy
0.04475575 - precision
0.46062847 - recall
0.08158455 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    141402|     53188
       1.0|      2918|      2492


#### Градиентный Бустинг

In [109]:
histboost = HistGradientBoostingClassifier(random_state=RANDOM_SEED)

In [111]:
%%time
histboost.fit(X_train_preprocessed, y_train);

CPU times: total: 52.6 s
Wall time: 12 s


In [112]:
print_metrics(histboost, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.029671595638735875
0.7061269569203708 - roc_auc на вероятностях

0.64778298 - roc_auc
0.65504000 - accuracy
0.04911499 - precision
0.64011091 - recall
0.09123001 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    127545|     67045
       1.0|      1947|      3463


#### [CatBoost](https://catboost.ai/) (CatBoost - открытая программная библиотека, разработанная компанией Яндекс и реализующая уникальный патентованный алгоритм построения моделей машинного обучения, использующий одну из оригинальных схем градиентного бустинга.)

In [113]:
catboost = CatBoostClassifier(
    iterations=100, verbose=False, random_state=RANDOM_SEED)

In [114]:
%%time
catboost.fit(X_train_preprocessed, y_train);

CPU times: total: 7.02 s
Wall time: 6.7 s


In [115]:
print_metrics(catboost, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.02825033404176709
0.7077386858895414 - roc_auc на вероятностях

0.64831355 - roc_auc
0.64208500 - accuracy
0.04836266 - precision
0.65489834 - recall
0.09007360 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    124874|     69716
       1.0|      1867|      3543


#### [XGBoost](https://github.com/dmlc/xgboost)

Основные особенности XGBoost, отличающие его от других алгоритмов градиентного бустинга, включают:

* Умная штрафовка деревьев
* Пропорциональное уменьшение узлов листьев
* Метод Ньютона в оптимизации
* Дополнительный параметр рандомизации
* Реализация на одиночных, распределенных системах и out-of-core вычислениях
* Автоматический отбор признаков

Предварительно устанавливается `pip install xgboost` согласно [документации](https://xgboost.readthedocs.io/en/stable/install.html#python)

In [116]:
xgboost = XGBClassifier()

In [117]:
%%time
xgboost.fit(X_train_preprocessed.values, y_train.values);

CPU times: total: 36.3 s
Wall time: 6.13 s


In [119]:
print_metrics(xgboost, X_valid_preprocessed.values, y_valid.values)

Порог перевода вероятностей в классы: 0.027880840510436353
0.7118732466452284 - roc_auc на вероятностях

0.65103815 - roc_auc
0.63270000 - accuracy
0.04816477 - precision
0.67042514 - recall
0.08987288 - f1

prediction|    0     |    1     
true label|          |          
--------------------------------
         0|    122913|     71677
         1|      1783|      3627


#### LGBMClassifier — это фреймворк, который предоставляет реализацию деревьев принятия решений с градиентным бустингом.

In [120]:
lightgbm = LGBMClassifier(random_state=RANDOM_SEED)

In [121]:
%%time
lightgbm.fit(X_train_preprocessed, y_train);

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 39494, number of negative: 1420548
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.052455 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 785
[LightGBM] [Info] Number of data points in the train set: 1460042, number of used features: 55
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.027050 -> initscore=-3.582649
[LightGBM] [Info] Start training from score -3.582649
CPU times: total: 15.4 s
Wall time: 2.75 s


In [122]:
print_metrics(lightgbm, X_valid_preprocessed, y_valid)

Порог перевода вероятностей в классы: 0.028808964224552883
0.7064644991759061 - roc_auc на вероятностях

0.64817318 - roc_auc
0.63831500 - accuracy
0.04811419 - precision
0.65859519 - recall
0.08967696 - f1

prediction|   0.0    |   1.0    
true label|          |          
--------------------------------
       0.0|    124100|     70490
       1.0|      1847|      3563


### Оптимизация модели  

Лучшей моделью является LightGBM по следующим причинам:
+ Один из лучших показателей `roc_auc`.
+ Быстрое обучение. 
+ Модель интерпретируема, то есть можно получить показатели важности признаков.
+ Может предсказывать вероятность класса.
+ Нет проблем с процессорами без SSE4 как у CatBoost.

Оптимизация модели и конвейера по подготовке данных проводится с помощью байесовской оптимизации. При разных гиперпараметрах модель обучается на тренировочных данных, а оценивается на валидационных.

In [133]:
def optimize_lightgbm(
    rare_encoder_tol: float, 
    constant_dropper_tol: float, 
    correlated_dropper_threshold: float, 
    n_estimators: float, 
    learning_rate: float, 
    reg_lambda: float, 
    num_leaves: float, 
    reg_alpha: float, 
    boosting_type: str = 'goss'
) -> float:
    """Используется Баейсовским оптимизатором для поиска лучших гиперпараметров 
    конвейера по подготовке данных и модели LGBMClassifier.
    """

    # Создадим конвейер с заданными гиперпараметрами
    model = Pipeline(steps=[
        # Создание дополнительных признаков
        ('indexer', FunctionTransformer(set_index)), 
        ('imputer', FunctionTransformer(fill_missings)), 
        ('engineer', FunctionTransformer(create_features)), 
        ('dropper', DropFeatures(['client_id', 'visit_date', 'visit_time', 
                                  'device_screen_resolution'])), 
        # Преобразования численных переменных
        ('normalization', YeoJohnsonTransformer()), 
        ('outlier_remover', Winsorizer()), 
        ('scaler', SklearnTransformerWrapper(StandardScaler())), 
        # Преобразования категориальных признаков
        ('rare_encoder', RareLabelEncoder(
            tol=rare_encoder_tol, replace_with='rare')),
        ('onehot_encoder', OneHotEncoder(drop_last_binary=True)), 
        ('bool_converter', FunctionTransformer(converse_types)), 
        # Удаление дубликатов и коррелируемых признаков
        ('constant_dropper', DropConstantFeatures(tol=constant_dropper_tol)), 
        ('duplicated_dropper', DropDuplicateFeatures()), 
        ('correlated_dropper', DropCorrelatedFeatures(
            threshold=correlated_dropper_threshold)), 
        # Лучшая модель с оптимизированными гиперпараметрами
        ('model', LGBMClassifier(
            n_estimators=int(n_estimators), boosting_type=boosting_type, 
            learning_rate=learning_rate, num_leaves=int(num_leaves), 
            reg_lambda=reg_lambda, reg_alpha=reg_alpha, 
            random_state=RANDOM_SEED))])
    
    # Обучим и оценим модель
    model.fit(X_train, y_train)
    prediction = model.predict_proba(X_valid)[:, 1]
    return roc_auc_score(y_valid, prediction)

In [135]:
X_train

session_id             client_id  \
1056663   547332070992313735.1638727047.1638727047      127435678.163873   
1409550  7049980726847853060.1629809978.1629809978     1641451550.162934   
739873   4064566220882386809.1639930788.1639930788      946355569.163992   
62902    1033849280328168809.1631647080.1631647080      240711793.163165   
1297234  6544287746962620171.1638268683.1638268683     1523710728.163827   
...                                            ...                   ...   
1793000  8755082352522037809.1633552946.1633552946     2038451459.163355   
207261   1682284231298311525.1640424805.1640424805  391687320.1640424805   
93412    1170303784354950884.1640345317.1640345317      272482583.164035   
1568591  7753976912353269271.1634047522.1634047522     1805363435.163405   
1119538  5753600408244704247.1626854393.1626854393     1339614486.162685   

         visit_date visit_time  visit_number            utm_source utm_medium  \
1056663  2021-12-05   20:57:27             1  ZpYIoDJMcFzVoPFsHGJL     banner   
1409550  2021-08-24   15:00:00             5  MvfHsxITijuriZxsqZqt        cpm   
739873   2021-12-19   19:19:48             2  ZpYIoDJMcFzVoPFsHGJL     banner   
62902    2021-09-14   22:00:00             1  ZpYIoDJMcFzVoPFsHGJL     banner   
1297234  2021-11-30   13:38:03             1  ZpYIoDJMcFzVoPFsHGJL     banner   
...             ...        ...           ...                   ...        ...   
1793000  2021-10-06   23:00:00             1  fDLlAcSmythWSCVMvqvL     (none)   
207261   2021-12-25   12:33:25             1  fDLlAcSmythWSCVMvqvL     (none)   
93412    2021-12-24   14:28:37             1  fDLlAcSmythWSCVMvqvL     (none)   
1568591  2021-10-12   17:00:00             1  ZpYIoDJMcFzVoPFsHGJL     banner   
1119538  2021-07-21   10:00:00             1  MvfHsxITijuriZxsqZqt        cpm   

                 utm_campaign         utm_adcontent           utm_keyword  \
1056663  TmThBvoCcwkCZZUWACYq  JNHcPlZPxEMWDnRiyoBf  puhZPIYqKXeFPaUviSjo   
1409550  FTjNLDyTrXaWYgZymFkV  PkybGvWbaqORmxjNunqZ                   NaN   
739873   LEoPHuyFvzoNfnzGgfcd  vCIpmpaGBnIQhyYNkXqp  puhZPIYqKXeFPaUviSjo   
62902    gecBYcKZCPMcVYdSSzKP  JNHcPlZPxEMWDnRiyoBf                   NaN   
1297234  LEoPHuyFvzoNfnzGgfcd  vCIpmpaGBnIQhyYNkXqp  puhZPIYqKXeFPaUviSjo   
...                       ...                   ...                   ...   
1793000  LTuZkdKfxRGVceoWkVyg  JNHcPlZPxEMWDnRiyoBf                   NaN   
207261   LTuZkdKfxRGVceoWkVyg  JNHcPlZPxEMWDnRiyoBf  puhZPIYqKXeFPaUviSjo   
93412    LTuZkdKfxRGVceoWkVyg  JNHcPlZPxEMWDnRiyoBf  puhZPIYqKXeFPaUviSjo   
1568591  gecBYcKZCPMcVYdSSzKP  JNHcPlZPxEMWDnRiyoBf                   NaN   
1119538  FTjNLDyTrXaWYgZymFkV  dUuXlWzvmhDSyclWRhNP                   NaN   

        device_category device_os device_brand device_model  \
1056663          mobile       iOS        Apple          NaN   
1409550          mobile       NaN       Xiaomi          NaN   
739873           mobile   Android      Samsung          NaN   
62902            mobile       NaN        Apple          NaN   
1297234          mobile   Android       Xiaomi          NaN   
...                 ...       ...          ...          ...   
1793000          mobile       NaN      Samsung          NaN   
207261           mobile       iOS        Apple          NaN   
93412           desktop   Windows          NaN          NaN   
1568591          mobile       NaN       Xiaomi          NaN   
1119538          mobile       NaN       Xiaomi          NaN   

        device_screen_resolution device_browser geo_country          geo_city  
1056663                  428x926         Safari      Russia       Novotroitsk  
1409550                  393x851         Chrome      Russia        Balashikha  
739873                   339x753         Chrome      Russia        Almetyevsk  
62902                    414x896         Safari      Russia  Saint Petersburg  
1297234                  393x851         Chrome      Russia            M

In [137]:
optimizing_parameters = {
    'rare_encoder_tol': (0.01, 0.1), 
    'constant_dropper_tol': (0.95, 0.999), 
    'correlated_dropper_threshold': (0.7, 0.99), 
    'n_estimators': (50, 5000), 
    'learning_rate': (0.01, 0.25), 
    'reg_lambda': (0, 50), 
    'num_leaves': (10, 120), 
    'reg_alpha': (0, 50)}

In [ ]:
# байесовский оптимизатор не работает с категориальными значениями, поэтому для 
# каждого типа бустинга будет проводится своя оптимизация гиперпараметров

best_score, best_parameters = 0.0, dict()
for boosting_type in ('gbdt', 'goss'):

    print(f'boosting_type = {boosting_type}')
    optimizer = BayesianOptimization(
        partial(optimize_lightgbm, boosting_type=boosting_type), 
        optimizing_parameters, random_state=RANDOM_SEED)
    optimizer.maximize(init_points=5, n_iter=10)
    
    if best_score < optimizer.max['target']:
        best_score = optimizer.max['target']
        best_parameters.update(optimizer.max['params'])
        best_parameters['boosting_type'] = boosting_type

boosting_type = gbdt
|   iter    |  target   | consta... | correl... | learni... | n_esti... | num_le... | rare_e... | reg_alpha | reg_la... |
-------------------------------------------------------------------------------------------------------------------------
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 39494, number of negative: 1420548
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.070861 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1232
[LightGBM] [Info] Number of data points in the train set: 1460042, number of used features: 57
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.027050 -> initscore=-3.582649
[LightGBM] [Info] Start training from score -3.582649
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warnin

In [ ]:
print(f'Лучшее значение метрики ROC-AUC={best_score} при параметрах:\n')
for param, value in best_parameters.items():
    print(f'{param} = {value}')

## Оценка модели

In [ ]:
final_pipeline = Pipeline(steps=[

    # Создание дополнительных признаков и
    # Приведение датафрейма к удобному виду 
    ('indexer', FunctionTransformer(set_index)), 
    ('imputer', FunctionTransformer(fill_missings)), 
    ('engineer', FunctionTransformer(create_features)), 
    ('dropper', DropFeatures(['client_id', 'visit_date', 'visit_time', 
                              'device_screen_resolution'])), 

    # Преобразования численных переменных
    ('normalization', YeoJohnsonTransformer()), 
    ('outlier_remover', Winsorizer()), 
    ('scaler', SklearnTransformerWrapper(StandardScaler())), 

    # Преобразования категориальных признаков
    ('rare_encoder', RareLabelEncoder(tol=0.047319, replace_with='rare')),
    ('onehot_encoder', OneHotEncoder(drop_last_binary=True)), 
    ('bool_converter', FunctionTransformer(converse_types)), 

    # Удаление дубликатов и коррелируемых признаков
    ('constant_dropper', DropConstantFeatures(tol=0.95579)), 
    ('duplicated_dropper', DropDuplicateFeatures()), 
    ('correlated_dropper', DropCorrelatedFeatures(threshold=0.8856)), 

    # Лучшая модель с оптимизированными гиперпараметрами
    ('model', LGBMClassifier(
        random_state=RANDOM_SEED, learning_rate=0.04440, boosting_type='gbdt', 
        n_estimators=4726, reg_lambda=38.7116, reg_alpha=13.22778, num_leaves=67)), 
    
])

### Метрики модели

Для оценки метрик модели обучим её на объектах тренировочной и валидационной выборках и сделаем предсказания на тестовых данных. 

Целевая метрика `roc-auc=0.6534` (для пресказанных классов) выбранной модели превосходит 0.65, а значит, цель работы выполнена.

Хотя метрика `f1=0.0849` довольно низкая, что неудивительно при большом количестве неверно классифицированных объектов нулевого класса.

У модели наблюдается совсем небольшое переобучение.

In [ ]:
final_pipeline.fit(X, y);

In [ ]:
test_proba = final_pipeline.predict_proba(X_test)[:, 1]
best_threshold = find_best_threshold(y_test, test_proba)
test_prediction = (test_proba > best_threshold).astype(int)

print(f'Лучший порог перевода вероятностей в класс: {best_threshold}')

In [ ]:
print(f'Метрики лучшей модели на обучающей выборке:')
print_metrics(final_pipeline, X, y, best_threshold)

In [ ]:
print(f'Метрики лучшей модели на тестовой выборке:')
print_metrics(
    final_pipeline, X_test, y_test, best_threshold, show_roc_curve=True)

### Обучение на всех данных

Для анализа обработки данных и важности признаков разобъём финальный конвейер на препроцессор и модель и обучим их на всех данных. А перед сохранением модели объединим обратно.

In [ ]:
final_model = final_pipeline.named_steps['model']
final_preprocessor = final_pipeline.set_params(model=None)

In [ ]:
sessions_preprocessed = final_preprocessor.fit_transform(sessions)

In [ ]:
final_model.fit(sessions_preprocessed, target);

### Анализ обработки данных

В итоге всех преобразований получается 62 признака, при том, что ещё 16 признаков были удалены из-за корреляций и т.п..

Датасет имеет 175 034 дубликатов, но как показали эксперименты, удаление дубликатов из тренировочной выборки ведёт к небольшому ухудшению метрик. 

Признаков, коррелируемых с целевой переменной, нет.

In [ ]:
sessions_preprocessed.shape

In [ ]:
sessions_preprocessed.info()

In [ ]:
print('Количество дубликатов:', sessions_preprocessed.duplicated().sum())

In [ ]:
print('Корреляция с целевой переменной:')
correlation = pd.concat([sessions_preprocessed, target], axis=1).corr()
correlation['target'].sort_values(ascending=False, key=abs).head(5)

### Важность признаков

Самыми важными признаками после преобразования оказались численные переменные: день (месяца и недели), час, минута (скорее всего именно нулевая минута часа) и номер посещения, размеры экрана и расстояние до Москвы.

После этих признаков важность остальных сильно падает. Возможно такова особенность работы с категориальными признаками (особенно с большим количеством неравномерно распределенных уникальных значений).

Самыми важными исходными признаками окзаались: размеры экрана, дата, время и номер посещения, город пользователя, а также признаки с дополнительными данными (как индикатор органического трафика). 

In [ ]:
print('Признаки, удалённые во время feature selection\n')
all = 0

for step in ('constant_dropper', 'duplicated_dropper', 'correlated_dropper'):
    print(step + ':')
    for column in final_preprocessor.named_steps[step].features_to_drop_:
        print(f'\t{column}')
        all += 1

print(f'Всего удалено: {all}')

In [ ]:
feature_importance = pd.Series(
    data=final_model.feature_importances_, 
    index=sessions_preprocessed.columns)

In [ ]:
plt.figure(figsize=(16, 10))
most_important = feature_importance.sort_values(ascending=False).head(25)
sns.barplot(x=most_important, y=most_important.index, orient='h')
plt.title('Самые важные признаки после преобразования');

In [ ]:
# Из важности производных признаков получим важность оригинальных
# Также получим важность признаков с добавленными данными '_added_'

original_columns = list(sessions.columns) + ['_added_']
column_importances = list()
for col in original_columns:
    imp = feature_importance[feature_importance.index.str.contains(col)].sum()
    column_importances.append(imp)

column_importances = pd.Series(column_importances, index=original_columns)
column_importances.sort_values(ascending=False, inplace=True)

In [ ]:
plt.figure(figsize=(18, 10))
sns.barplot(x=column_importances, y=column_importances.index, orient='h')
plt.title('Важность оригинальных признаков');

### Сохранение модели

In [ ]:
# Объединим препроцессор и модель обратно

final_pipeline = final_preprocessor.set_params(model=final_model)

In [ ]:
# Добавим метаданные для модели

metadata = {
    'name': 'SberAutopodpiska: target event prediction', 
    'descripton': ('Модель по предсказанию совершения пользователем одного из '
                   'целевых действий "Заказать звонок" или "Оставить заявку" '
                   'на сайте сервиса СберАвтоподписка.'), 
    'model_type': final_model.__class__.__name__, 
    'version': 1.1, 
    'training_datetime': datetime.now(), 
    'author': 'Demir Uzun', 
    'threshold': best_threshold, 
    'metrics': {
        'roc_auc': roc_auc_score(y_test, test_proba), 
        'roc_auc_by_class': roc_auc_score(y_test, test_prediction),
        'accuracy': accuracy_score(y_test, test_prediction), 
        'precision': precision_score(y_test, test_prediction), 
        'recall': recall_score(y_test, test_prediction), 
        'f1': f1_score(y_test, test_prediction),
    }
}

final_pipeline.metadata = metadata

In [ ]:
# Сохраним модель

models_folder.mkdir(exist_ok=True)
filename = f'model_{datetime.now():%Y%m%d%H%M%S}.pkl'

with open(models_folder / filename, 'wb') as file:
    dill.dump(final_pipeline, file)

## Выводы

Для преобразования входных данных, со структурой как в файле `ga_sessions.csv`, в удобный для предсказания вид понадобилось четыре этапа:
1. Заполнение пропусков и генерация признаков. В том числе добавление новых данных, как-то органический трафик или расстояние до Москвы.
2. Преобразование численных переменных: нормализация и удаление выбросов.
3. Преобразование категориальных признаков. Основная сложность с ними была в многообразии редких уникальных значений. В итоге только самые популярные значения были закодированы методом one-hot.
4. Удаление дублирующих и коррелируемых признаков. Признаки могут коррелировать до 0.95, но именно с таким порогом финальная модель даёт лучший результат.

Было проверено 10 моделей с гиперпараметрами по умолчанию. В тройке лучших оказались алгоритмы бустинга от sklearn, lightgbm и catboost.

В итоге в качестве лучшей модели был выбран `LightGBM` по следующим причинам: 
+ Один из лучших показателей `roc_auc`.
+ Быстрое обучение. 
+ Модель интерпретируема, то есть можно получить показатели важности признаков.
+ Может предсказывать вероятность класса.
+ Нет проблем с процессорами без SSE4 как у CatBoost.

Шаг оптимизации модели помог выбрать лучшие гиперпараметры для модели: n_estimators=800, learning_rate=0.07, reg_lambda=10, num_leaves=26, reg_alpha=10, boosting_type='goss'.

Качество модели по метрике `roc-auc` составляет **0.7148** (0.6535 при предсказании классов). Но метрика `f1`=0.0871 оставляет желать лучшего. Тем не менее, переобучения нет и цель проекта выполнена - `roc-auc` > 0.65.

Для улучшения качества предсказания можно было бы: 
1. Увеличить количество данных. Тестовая выборка пойдёт на дообучение модели, так что может модель будет лучше в конечном итоге.
2. Провести ребалансировку классов. Но если уменьшить выборку с отрицательной целевой переменной, то модель теряет в качестве, а если увеличивать выборку с положительным классом, то модели обучаются слишком долго. 
3. Провести более тщательный поиск наилучших гиперпараметров - это займёт много времени, а прирост качества будет небольшим. 
4. Провести дополнительную генерацию признаков. Но хорошие идеи придумывать сложно.
5. Попробовать более сложные модели, например, нейронные сети глубокого обучения. 

In [ ]:
import json


In [ ]:
with open('data/exemples/examples.json', 'rb') as file:
    examples = json.load(file)

In [ ]:
print('Запрос предсказания класса для одного объекта.')
data = json.dumps(examples[0])#.encode("utf-8")

In [ ]:
#df = pd.DataFrame.from_dict([examples[0]])
df = pd.DataFrame.from_dict(examples)

In [ ]:
df.shape

In [ ]:
y = model['model'].predict_proba(data)[:, 1]

In [ ]:
data.reshape(-1, 1)

In [ ]:
my_pipi = Pipeline(steps=[

    # Создание дополнительных признаков и
    # Приведение датафрейма к удобному виду 
    ('indexer', FunctionTransformer(set_index)), 
    ('imputer', FunctionTransformer(fill_missings)), 
    ('engineer', FunctionTransformer(create_features)), 
    ('dropper', DropFeatures(['client_id', 'visit_date', 'visit_time', 
                              'device_screen_resolution'])), 

    # Преобразования численных переменных
    ('normalization', YeoJohnsonTransformer()), 
    ('outlier_remover', Winsorizer()), 
    ('scaler', SklearnTransformerWrapper(StandardScaler())), 

    # Преобразования категориальных признаков
    ('rare_encoder', RareLabelEncoder(tol=0.047319, replace_with='rare')),
    ('onehot_encoder', OneHotEncoder(drop_last_binary=True)), 
    ('bool_converter', FunctionTransformer(converse_types)), 

    # Удаление дубликатов и коррелируемых признаков
    ('constant_dropper', DropConstantFeatures(tol=0.95579)), 
    ('duplicated_dropper', DropDuplicateFeatures()), 
    ('correlated_dropper', DropCorrelatedFeatures(threshold=0.8856)), 

    # # Лучшая модель с оптимизированными гиперпараметрами
    # ('model', LGBMClassifier(
    #     random_state=RANDOM_SEED, learning_rate=0.04440, boosting_type='gbdt', 
    #     n_estimators=4726, reg_lambda=38.7116, reg_alpha=13.22778, num_leaves=67)), 
    
])

In [ ]:
my_pipi

In [ ]:
d = my_pipi.fit(df)

In [ ]:
d

In [ ]:
wwwwww = df.iloc[[0]]

In [ ]:
wwwwww

In [ ]:
we = preprocessor.fit_transform(df)
# we3 = preprocessor.transform(df)

# print(f'X_train.shape = {we.shape}')

In [ ]:
we